## Buy Box Datenanalyse

In [99]:
import pandas as pd
import numpy as np

df = pd.read_csv('cleaned_data.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109323 entries, 0 to 109322
Data columns (total 22 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   asin                  109323 non-null  object 
 1   time                  109323 non-null  object 
 2   id                    109323 non-null  float64
 3   price                 109323 non-null  float64
 4   currency              109323 non-null  object 
 5   crawlTime             109323 non-null  object 
 6   condition             109323 non-null  object 
 7   sellerName            109323 non-null  object 
 8   sellerId              109323 non-null  object 
 9   sellerbewertung       82422 non-null   float64
 10  seller_sterne         109323 non-null  float64
 11  lieferdatum           105495 non-null  object 
 12  lieferpreis           105495 non-null  float64
 13  lieferung_durch       109323 non-null  object 
 14  ranking               109323 non-null  float64
 15  

In [100]:
df.head()

asin                 time       id  price currency  \
0  B00000JD6K  2023-03-19 13:00:00   1919.0   95.0        €   
1  B00000JD6K  2023-03-19 13:00:00   2375.0   86.9        €   
2  B00000JD6K  2023-03-19 14:00:00  11131.0   95.8        €   
3  B00000JD6K  2023-03-19 14:00:00  11585.0   86.9        €   
4  B00000JD6K  2023-03-19 15:00:00  20373.0   95.8        €   

                    crawlTime condition                 sellerName  \
0  2023-03-19 13:31:27.889305       Neu                      Kidia   
1  2023-03-19 13:31:28.080901       Neu  STILE IMMAGINE DIGITAL HD   
2  2023-03-19 14:36:46.595551       Neu                      Kidia   
3  2023-03-19 14:36:46.805501       Neu  STILE IMMAGINE DIGITAL HD   
4  2023-03-19 15:43:49.220017       Neu                      Kidia   

         sellerId  sellerbewertung  ...  lieferpreis  \
0  A2XUKJNGI8V9XU            46.56  ...          0.0   
1  A16E8RFMSALSSB            28.13  ...          9.9   
2  A2XUKJNGI8V9XU            46.56  ...          0.0   
3  A16E8RFMSALSSB            28.13  ...          9.9   
4  A2XUKJNGI8V9XU            46.56  ...          0.0   

             lieferung_durch  ranking buyBoxWinner  numberOfSellers  \
0                     Amazon      0.0         True              2.0   
1  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
2                     Amazon      0.0         True              2.0   
3  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
4                     Amazon      0.0         True              2.0   

   trigByReactive  time_gap  copyed_cause_missing  Fulfillment_type  date_diff  
0           False       0.0                 False               FBA        3.0  
1           False       0.0                 False               FBM        7.0  
2           False       0.0                 False               FBA        3.0  
3           False       0.0                 False               FBM       27.0  
4           False       0.0                 False               FBA        3.0  

[5 rows x 22 columns]

In [101]:
buy_box_counts = df['buyBoxWinner'].value_counts()
buy_box_counts

False    98728
True     10595
Name: buyBoxWinner, dtype: int64

## Generating Lists Of Asins Where Amazon is Present as a Seller and where Not

In [102]:
amazon_asin_values = df.loc[df['sellerName'].isin(['amazon', 'Amazon Warehouse', 'Amazon US', 'Amazon UK']), 'asin'].unique()
print(f"An so vielen Asins ist Amazon als Verkäufer eingetragen:{len(amazon_asin_values)}")

# Assuming the DataFrame is named 'df'
all_asin_values = df['asin'].unique()

# Subtract the values that exist in the 'amazon_asin_values' list
non_amazon_asin_values = set(all_asin_values) - set(amazon_asin_values)
print(f"An so vielen Asins ist Amazon nicht als Verkäufer eingetragen:{len(non_amazon_asin_values)}")
print(f"So Viele unterschiedliche Asins gibt es maximal {len(all_asin_values)}")

An so vielen Asins ist Amazon als Verkäufer eingetragen:628
An so vielen Asins ist Amazon nicht als Verkäufer eingetragen:354
So Viele unterschiedliche Asins gibt es maximal 982


## Vergleich wie Oft die Seller die BuyBox gewinnen wenn Amazon nicht dabei ist.

In [103]:
## Vergleich wie Oft die Seller die BuyBox gewinnen wenn Amazon dabei ist, nicht dabei ist.
##Wie oft Seller unter Sich gewinnen
# Get the rows where the asin is in 'non_amazon_asin_values' and the 'buyBoxWinner' column is True
df_non_amazon_buy_box_winners = df.loc[(df['asin'].isin(non_amazon_asin_values)) & (df['buyBoxWinner'] == True)]
amazon_seller_names = ['amazon', 'Amazon Warehouse', 'Amazon US', 'Amazon UK']

# Get the total count of rows where the asin is in 'non_amazon_asin_values' and the 'buyBoxWinner' column is True
total_count = len(df_non_amazon_buy_box_winners)

# Get the count of rows where the value in the 'sellerName' column is not in the 'amazon_seller_names' list
seller_count = len(df_non_amazon_buy_box_winners.loc[~df_non_amazon_buy_box_winners['sellerName'].isin(amazon_seller_names)])

# Calculate the percentage
if total_count > 0:
    percentage = (seller_count / total_count) * 100
else:
    percentage = 0

# Print the percentage
print(percentage)


100.0


## Wie oft FremdSeller die BuyBox gewinnen wenn Amazon dabei ist

In [104]:
#Wie oft Seller mit Amazon gewinnen
# Get the rows where the asin is in 'amazon_asin_values' and the 'buyBoxWinner' column is True
df_amazon_buy_box_winners = df.loc[(df['asin'].isin(amazon_asin_values)) & (df['buyBoxWinner'] == True)]

# Get the total count of rows where the asin is in 'amazon_asin_values' and the 'buyBoxWinner' column is True
total_count = len(df_amazon_buy_box_winners)
print(f"The Number of BuyBoxWinning Rows where Amazon as a seller is present {total_count}")

# Get the count of rows where the value in the 'sellerName' column is not 'amazon' or 'Amazon Warehouse'
offer_without_amazon = df_amazon_buy_box_winners.loc[(df_amazon_buy_box_winners['sellerName'] != 'amazon') & (df_amazon_buy_box_winners['sellerName'] != 'Amazon Warehouse')]
#print(offer_without_amazon)
seller_count = len(offer_without_amazon)
print(f"The Number of BuyBoxWinning Rows where Amazon is not the winner is {seller_count}")

offer_without_amazon = df_amazon_buy_box_winners.loc[(df_amazon_buy_box_winners['sellerName'] == 'amazon') | (df_amazon_buy_box_winners['sellerName'] == 'Amazon Warehouse')]
print(f"The Number of BuyBoxWinning Rows where Amazon is the winner is {len(offer_without_amazon)}")
# Calculate the percentage
if total_count > 0:
    percentage = (seller_count / total_count) * 100
else:
    percentage = 0

# Print the percentage
print(percentage)


The Number of BuyBoxWinning Rows where Amazon as a seller is present 7276
The Number of BuyBoxWinning Rows where Amazon is not the winner is 1128
The Number of BuyBoxWinning Rows where Amazon is the winner is 6148
15.503023639362286


In [105]:
##Lets Watch the Rows where Amazon US and Amazon UK are Present
#Hier sieht man das Amazon UK und Amazon US nur sehr geringen Anteil an BuyBox haben.
df_amazon_uk_us = df_amazon_buy_box_winners.loc[(df_amazon_buy_box_winners['sellerName'] == 'Amazon UK') | (df_amazon_buy_box_winners['sellerName'] == 'Amazon US')]
print(len(df_amazon_uk_us))
#df_amazon_uk_us

50


## Wie oft ist der niedrigste Preis auch der Gewinner?

In [106]:
# Convert the 'timestamp' column to a DatetimeIndex
df["time"] = pd.to_datetime(df["time"], format="%Y-%m-%d %H:%M:%S")
# Group the DataFrame by 'asin' and time slot (hour)
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the percentage of times the cheapest price is the buyBoxWinner
def cheapest_is_buy_box_winner(group):
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    # Check if the buyBoxWinner is True for the cheapest price row
    cheapest_bb_winner = cheapest_row.iloc[0]['buyBoxWinner']
    # Calculate the percentage
    if cheapest_bb_winner:
        return 1
    else:
        return 0

# Apply the custom function to each group
percentages = grouped_df.apply(cheapest_is_buy_box_winner)

# Calculate the overall percentage
overall_percentage = percentages.mean() * 100

# Print the overall percentage
print(overall_percentage)

66.36548852865621


In [107]:
# Convert the 'timestamp' column to a DatetimeIndex
df["time"] = pd.to_datetime(df["time"], format="%Y-%m-%d %H:%M:%S")
# Group the DataFrame by 'asin' and time slot (hour)
#Only use New Offers, cause used objects arent obligated to win the buyBox
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the percentage of times the cheapest price is not the buyBoxWinner
def cheapest_not_buy_box_winner(group):
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    #print(cheapest_row[['asin', 'price', 'time','buyBoxWinner']])
    most_expensive_row = group.loc[group['price'] == group['price'].max()]
    #print(most_expensive_row[['asin', 'price', 'time','buyBoxWinner']])
    #print("--------------------------------------------")

    # Check if the buyBoxWinner is True for the cheapest price row
    cheapest_bb_winner = cheapest_row.iloc[0]['buyBoxWinner']
    # Calculate the percentage
    if not cheapest_bb_winner:
        return 1
    else:
        return 0

# Apply the custom function to each group
percentages = grouped_df.apply(cheapest_not_buy_box_winner)

# Calculate the overall percentage
overall_percentage = percentages.mean() * 100

# Print the overall percentage
print(overall_percentage)

33.634511471343785


In [108]:
df = pd.read_csv('cleaned_data.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109323 entries, 0 to 109322
Data columns (total 22 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   asin                  109323 non-null  object 
 1   time                  109323 non-null  object 
 2   id                    109323 non-null  float64
 3   price                 109323 non-null  float64
 4   currency              109323 non-null  object 
 5   crawlTime             109323 non-null  object 
 6   condition             109323 non-null  object 
 7   sellerName            109323 non-null  object 
 8   sellerId              109323 non-null  object 
 9   sellerbewertung       82422 non-null   float64
 10  seller_sterne         109323 non-null  float64
 11  lieferdatum           105495 non-null  object 
 12  lieferpreis           105495 non-null  float64
 13  lieferung_durch       109323 non-null  object 
 14  ranking               109323 non-null  float64
 15  

## Exclude Not New Offers and Reactive Offers

In [109]:
## Exclude all Rows where condition isnt New and which where a reactive Crawl
df = df[df['trigByReactive'] != True]
df = df[df['condition'].isin(['Neu', 'New'])]

### Wie hoch ist der Unterschied zwischen Maximalen Offerpreis und Minimalen Offerpreis. Absolut und Prozentual

In [110]:
### Wie hoch ist der Unterschied zwischen Maximalen Offerpreis und BuyBoxPreis. Absolut, Prozentual, Median, Durchschnitt
# Convert the 'timestamp' column to a DatetimeIndex
df["time"] = pd.to_datetime(df["time"], format="%Y-%m-%d %H:%M:%S")

# Group the DataFrame by 'asin' and time slot (hour)
# Only use New Offers, because used objects are not obligated to win the buyBox
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the difference between the highest and cheapest price
def difference_between_highest_and_cheapest(group):
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    # Get the row with the highest price
    highest_row = group.loc[group['price'] == group['price'].max()]
    # Calculate the difference between the highest price and the cheapest price
    difference = highest_row.iloc[0]['price'] - cheapest_row.iloc[0]['price']
    # Return the difference as a single value
    print("--------------------------------------------")
    print(cheapest_row[['asin', 'price', 'time','buyBoxWinner']])
    print(highest_row[['asin', 'price', 'time','buyBoxWinner']])
    print(difference)
    print("--------------------------------------------")
    return difference

# Apply the custom function to each group
results = grouped_df.apply(difference_between_highest_and_cheapest)

# Find the row/asin with the highest difference
highest_difference = results.max()
highest_difference_row = results.idxmax()

# Print the results
#print("Highest Difference:", highest_difference)
#print("Highest Difference Row/Asin:", highest_difference_row)


--------------------------------------------
         asin  price                time  buyBoxWinner
1  B00000JD6K   86.9 2023-03-19 13:00:00         False
         asin  price                time  buyBoxWinner
0  B00000JD6K   95.0 2023-03-19 13:00:00          True
8.099999999999994
--------------------------------------------
--------------------------------------------
         asin  price                time  buyBoxWinner
3  B00000JD6K   86.9 2023-03-19 14:00:00         False
         asin  price                time  buyBoxWinner
2  B00000JD6K   95.8 2023-03-19 14:00:00          True
8.899999999999991
--------------------------------------------
--------------------------------------------
         asin  price                time  buyBoxWinner
5  B00000JD6K   86.9 2023-03-19 15:00:00         False
         asin  price                time  buyBoxWinner
4  B00000JD6K   95.8 2023-03-19 15:00:00          True
8.899999999999991
--------------------------------------------
----------------

--------------------------------------------
           asin  price                time  buyBoxWinner
996  B0001GRVJQ  55.31 2023-03-19 17:00:00          True
            asin  price                time  buyBoxWinner
1002  B0001GRVJQ  104.7 2023-03-19 17:00:00         False
49.39
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
100085  B0001GRVJQ  55.31 2023-03-19 18:00:00          True
              asin  price                time  buyBoxWinner
100091  B0001GRVJQ  104.7 2023-03-19 18:00:00         False
49.39
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
1004  B0001GRVJQ  55.31 2023-03-19 19:00:00          True
            asin  price                time  buyBoxWinner
1010  B0001GRVJQ  104.7 2023-03-19 19:00:00         False
49.39
--------------------------------------------
----------

            asin  price                time  buyBoxWinner
2824  B000B2Q2MC  76.02 2023-03-19 16:00:00         False
26.599999999999994
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
100258  B000B2Q2MC  49.42 2023-03-19 18:00:00          True
              asin  price                time  buyBoxWinner
100262  B000B2Q2MC  76.02 2023-03-19 18:00:00         False
26.599999999999994
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
2825  B000B2Q2MC  49.42 2023-03-19 19:00:00          True
            asin  price                time  buyBoxWinner
2829  B000B2Q2MC  76.02 2023-03-19 19:00:00         False
26.599999999999994
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
2830  B000B2Q2MC  49.42 202

--------------------------------------------
            asin  price                time  buyBoxWinner
3330  B000GISU1M  74.99 2023-03-19 13:00:00          True
            asin  price                time  buyBoxWinner
3334  B000GISU1M  91.99 2023-03-19 13:00:00         False
17.0
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
3339  B000GISU1M  74.99 2023-03-19 14:00:00          True
            asin  price                time  buyBoxWinner
3343  B000GISU1M  91.99 2023-03-19 14:00:00         False
17.0
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
3348  B000GISU1M  74.99 2023-03-19 15:00:00          True
            asin  price                time  buyBoxWinner
3352  B000GISU1M  91.99 2023-03-19 15:00:00         False
17.0
--------------------------------------------
-------------------

--------------------------------------------
            asin  price                time  buyBoxWinner
3928  B000MJR8UO  245.3 2023-03-19 13:00:00          True
            asin   price                time  buyBoxWinner
3930  B000MJR8UO  387.45 2023-03-19 13:00:00         False
142.14999999999998
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
3931  B000MJR8UO  245.3 2023-03-19 14:00:00          True
            asin   price                time  buyBoxWinner
3933  B000MJR8UO  387.45 2023-03-19 14:00:00         False
142.14999999999998
--------------------------------------------
--------------------------------------------
            asin   price                time  buyBoxWinner
3934  B000MJR8UO  243.26 2023-03-19 15:00:00          True
            asin   price                time  buyBoxWinner
3936  B000MJR8UO  387.45 2023-03-19 15:00:00         False
144.19
--------------------------

...

--------------------------------------------
             asin   price                time  buyBoxWinner
96645  B09ZHWD8BZ  319.56 2023-03-19 23:00:00          True
             asin   price                time  buyBoxWinner
96655  B09ZHWD8BZ  456.29 2023-03-19 23:00:00         False
136.73000000000002
--------------------------------------------
--------------------------------------------
             asin   price       time  buyBoxWinner
96656  B09ZHWD8BZ  319.56 2023-03-20          True
             asin   price       time  buyBoxWinner
96656  B09ZHWD8BZ  319.56 2023-03-20          True
0.0
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
96657  B09ZHZGM8Q   56.2 2023-03-19 13:00:00          True
             asin  price                time  buyBoxWinner
96659  B09ZHZGM8Q  60.01 2023-03-19 13:00:00         False
3.809999999999995
--------------------------------------------
---------

--------------------------------------------
             asin   price                time  buyBoxWinner
97086  B0B2X4GM2V  113.84 2023-03-19 23:00:00          True
             asin  price                time  buyBoxWinner
97116  B0B2X4GM2V  228.5 2023-03-19 23:00:00         False
114.66
--------------------------------------------
--------------------------------------------
             asin   price       time  buyBoxWinner
97117  B0B2X4GM2V  113.84 2023-03-20          True
             asin   price       time  buyBoxWinner
97117  B0B2X4GM2V  113.84 2023-03-20          True
0.0
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
97118  B0B4KBSVK3  80.47 2023-03-19 13:00:00          True
             asin  price                time  buyBoxWinner
97119  B0B4KBSVK3  83.64 2023-03-19 13:00:00         False
3.1700000000000017
--------------------------------------------
----------------------

--------------------------------------------
             asin   price                time  buyBoxWinner
97287  B0B7WNRYZ8  201.53 2023-03-19 19:00:00          True
             asin   price                time  buyBoxWinner
97289  B0B7WNRYZ8  271.26 2023-03-19 19:00:00         False
69.72999999999999
--------------------------------------------
--------------------------------------------
             asin   price                time  buyBoxWinner
97290  B0B7WNRYZ8  201.53 2023-03-19 20:00:00          True
             asin   price                time  buyBoxWinner
97292  B0B7WNRYZ8  271.26 2023-03-19 20:00:00         False
69.72999999999999
--------------------------------------------
--------------------------------------------
             asin   price                time  buyBoxWinner
97293  B0B7WNRYZ8  199.85 2023-03-19 21:00:00          True
             asin  price                time  buyBoxWinner
97295  B0B7WNRYZ8  269.0 2023-03-19 21:00:00         False
69.15
---------------

             asin   price                time  buyBoxWinner
98111  B0B9GJLV2D  115.86 2023-03-19 23:00:00          True
             asin   price                time  buyBoxWinner
98140  B0B9GJLV2D  181.49 2023-03-19 23:00:00         False
65.63000000000001
--------------------------------------------
--------------------------------------------
             asin   price       time  buyBoxWinner
98142  B0B9GJLV2D  115.86 2023-03-20          True
             asin   price       time  buyBoxWinner
98161  B0B9GJLV2D  163.12 2023-03-20         False
47.260000000000005
--------------------------------------------
--------------------------------------------
             asin   price                time  buyBoxWinner
98173  B0B9XXTN28  654.46 2023-03-19 13:00:00          True
             asin   price                time  buyBoxWinner
98173  B0B9XXTN28  654.46 2023-03-19 13:00:00          True
0.0
--------------------------------------------
--------------------------------------------
     

--------------------------------------------
             asin  price                time  buyBoxWinner
98649  B0BDJJY92W  493.1 2023-03-19 22:00:00          True
             asin  price                time  buyBoxWinner
98649  B0BDJJY92W  493.1 2023-03-19 22:00:00          True
0.0
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
98669  B0BDJJY92W  493.1 2023-03-19 23:00:00          True
             asin  price                time  buyBoxWinner
98669  B0BDJJY92W  493.1 2023-03-19 23:00:00          True
0.0
--------------------------------------------
--------------------------------------------
             asin  price       time  buyBoxWinner
98688  B0BDJJY92W  489.0 2023-03-20          True
             asin   price       time  buyBoxWinner
98698  B0BDJJY92W  581.92 2023-03-20         False
92.91999999999996
--------------------------------------------
------------------------------

In [111]:
# Print the results
print("Highest Difference:", highest_difference)
print("Highest Difference Row/Asin:", highest_difference_row)

Highest Difference: 812.45
Highest Difference Row/Asin: ('B07KSBWFZS', Timestamp('2023-03-19 15:00:00', freq='H'))


## Prozentualer Unterschied zwischen minimalen und maximalen Preis

In [112]:
# Convert the 'timestamp' column to a DatetimeIndex
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Group the DataFrame by 'asin' and time slot (hour)
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the average percentage difference between the Price of the buyBoxWinning Row and the most expensive row
def avg_price_diff(group):
    # Get the row with the highest price
    highest_price_row = group.loc[group['price'] == group['price'].max()]
    highest_price = highest_price_row.iloc[0]['price']
    
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    cheapest_price = cheapest_row.iloc[0]['price']
    
    # Check if the buyBoxWinner is True for the cheapest price row
    cheapest_bb_winner = cheapest_row.iloc[0]['buyBoxWinner']
    
    # Calculate the percentage difference
    if cheapest_bb_winner:
        diff_percent = ((highest_price - cheapest_price) / highest_price) * 100
        return diff_percent
    else:
        return None

# Apply the custom function to each group
price_diffs = grouped_df.apply(avg_price_diff)

# Calculate the overall average percentage difference
overall_avg_diff = price_diffs.mean()

# Print the overall average percentage difference
print(overall_avg_diff)


22.80130606916724


### Wie hoch ist der Unterschied zwischen Maximalen Offerpreis und BuyBoxWinning Preis. Absolut und Prozentual

In [113]:
# Convert the 'time' column to a DatetimeIndex
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Group the DataFrame by 'asin' and time slot (hour)
# Only use New Offers, because used objects are not obligated to win the buyBox
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the difference between the highest and buyBox winning price
def difference_between_highest_and_buyBoxWinner(group):
    # Get the row with the buyBox winning offer
    buyBox_winner_row = group.loc[group['buyBoxWinner'] == True]
    # Check if there is a buyBox winner for the group
    if buyBox_winner_row.empty:
        return None
    # Get the row with the highest price
    highest_price_row = group.loc[group['price'] == group['price'].max()]
    # Calculate the difference between the highest price and the buyBox winning price
    difference = highest_price_row.iloc[0]['price'] - buyBox_winner_row.iloc[0]['price']
    # Return the difference as a single value
    print("--------------------------------------------")
    print(buyBox_winner_row[['asin', 'price', 'time', 'buyBoxWinner']])
    print(highest_price_row[['asin', 'price', 'time', 'buyBoxWinner']])
    print(difference)
    print("--------------------------------------------")
    return difference

# Apply the custom function to each group
results = grouped_df.apply(difference_between_highest_and_buyBoxWinner)

# Drop the groups where there is no buyBox winner
results = results.dropna()

# Find the row/asin with the highest difference
highest_difference = results.max()
highest_difference_row = results.idxmax()

# Print the results
#print("Highest Difference:", highest_difference)
#print("Highest Difference Row/Asin:", highest_difference_row)


--------------------------------------------
         asin  price                time  buyBoxWinner
0  B00000JD6K   95.0 2023-03-19 13:00:00          True
         asin  price                time  buyBoxWinner
0  B00000JD6K   95.0 2023-03-19 13:00:00          True
0.0
--------------------------------------------
--------------------------------------------
         asin  price                time  buyBoxWinner
2  B00000JD6K   95.8 2023-03-19 14:00:00          True
         asin  price                time  buyBoxWinner
2  B00000JD6K   95.8 2023-03-19 14:00:00          True
0.0
--------------------------------------------
--------------------------------------------
         asin  price                time  buyBoxWinner
4  B00000JD6K   95.8 2023-03-19 15:00:00          True
         asin  price                time  buyBoxWinner
4  B00000JD6K   95.8 2023-03-19 15:00:00          True
0.0
--------------------------------------------
--------------------------------------------
         asin

--------------------------------------------
           asin  price                time  buyBoxWinner
964  B0001GRVJQ  55.31 2023-03-19 13:00:00          True
           asin  price                time  buyBoxWinner
970  B0001GRVJQ  104.7 2023-03-19 13:00:00         False
49.39
--------------------------------------------
--------------------------------------------
           asin  price                time  buyBoxWinner
972  B0001GRVJQ  55.31 2023-03-19 14:00:00          True
           asin  price                time  buyBoxWinner
978  B0001GRVJQ  104.7 2023-03-19 14:00:00         False
49.39
--------------------------------------------
--------------------------------------------
           asin  price                time  buyBoxWinner
980  B0001GRVJQ  55.31 2023-03-19 15:00:00          True
           asin  price                time  buyBoxWinner
986  B0001GRVJQ  104.7 2023-03-19 15:00:00         False
49.39
--------------------------------------------
----------------------------

            asin  price                time  buyBoxWinner
3326  B000EENFIG  45.28 2023-03-19 23:00:00         False
8.719999999999999
--------------------------------------------
--------------------------------------------
            asin  price       time  buyBoxWinner
3327  B000EENFIG  36.56 2023-03-20          True
            asin  price       time  buyBoxWinner
3329  B000EENFIG  45.28 2023-03-20         False
8.719999999999999
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
3330  B000GISU1M  74.99 2023-03-19 13:00:00          True
            asin  price                time  buyBoxWinner
3334  B000GISU1M  91.99 2023-03-19 13:00:00         False
17.0
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
3339  B000GISU1M  74.99 2023-03-19 14:00:00          True
            asin  price      

            asin  price                time  buyBoxWinner
6947  B002BA58TA  48.94 2023-03-19 13:00:00          True
            asin  price                time  buyBoxWinner
6957  B002BA58TA   87.4 2023-03-19 13:00:00         False
38.46000000000001
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
6958  B002BA58TA  48.94 2023-03-19 14:00:00          True
            asin  price                time  buyBoxWinner
6968  B002BA58TA   87.4 2023-03-19 14:00:00         False
38.46000000000001
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
6969  B002BA58TA  48.94 2023-03-19 15:00:00          True
            asin  price                time  buyBoxWinner
6979  B002BA58TA   87.4 2023-03-19 15:00:00         False
38.46000000000001
--------------------------------------------
-------------------------

            asin   price       time  buyBoxWinner
8024  B0037LGH1K  114.08 2023-03-20          True
            asin   price       time  buyBoxWinner
8041  B0037LGH1K  198.85 2023-03-20         False
84.77
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
8055  B0037LIMOA  95.96 2023-03-19 13:00:00          True
            asin   price                time  buyBoxWinner
8075  B0037LIMOA  185.54 2023-03-19 13:00:00         False
89.58
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
8086  B0037LIMOA  95.17 2023-03-19 14:00:00          True
            asin   price                time  buyBoxWinner
8106  B0037LIMOA  185.54 2023-03-19 14:00:00         False
90.36999999999999
--------------------------------------------
--------------------------------------------
            asin  price         

...

--------------------------------------------
             asin  price                time  buyBoxWinner
85923  B09N4SJLWM  79.06 2023-03-19 13:00:00          True
             asin   price                time  buyBoxWinner
85943  B09N4SJLWM  120.49 2023-03-19 13:00:00         False
41.42999999999999
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
85954  B09N4SJLWM  79.06 2023-03-19 14:00:00          True
             asin   price                time  buyBoxWinner
85973  B09N4SJLWM  120.49 2023-03-19 14:00:00         False
41.42999999999999
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
85981  B09N4SJLWM  79.06 2023-03-19 15:00:00          True
             asin   price                time  buyBoxWinner
86000  B09N4SJLWM  120.49 2023-03-19 15:00:00         False
41.42999999999999
-------

--------------------------------------------
             asin  price                time  buyBoxWinner
87444  B09NVY73WQ  499.0 2023-03-19 19:00:00          True
             asin   price                time  buyBoxWinner
87454  B09NVY73WQ  832.94 2023-03-19 19:00:00         False
333.94000000000005
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
87455  B09NVY73WQ  499.0 2023-03-19 20:00:00          True
             asin   price                time  buyBoxWinner
87466  B09NVY73WQ  830.93 2023-03-19 20:00:00         False
331.92999999999995
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
87467  B09NVY73WQ  499.0 2023-03-19 21:00:00          True
             asin   price                time  buyBoxWinner
87477  B09NVY73WQ  832.94 2023-03-19 21:00:00         False
333.94000000000005
----

             asin  price                time  buyBoxWinner
96386  B09ZD4LFR3  486.9 2023-03-19 19:00:00         False
96392  B09ZD4LFR3  486.9 2023-03-19 19:00:00         False
213.01999999999998
--------------------------------------------
--------------------------------------------
             asin   price                time  buyBoxWinner
96393  B09ZD4LFR3  276.18 2023-03-19 20:00:00          True
             asin  price                time  buyBoxWinner
96409  B09ZD4LFR3  486.9 2023-03-19 20:00:00         False
210.71999999999997
--------------------------------------------
--------------------------------------------
             asin   price                time  buyBoxWinner
96410  B09ZD4LFR3  273.88 2023-03-19 21:00:00          True
             asin  price                time  buyBoxWinner
96426  B09ZD4LFR3  486.9 2023-03-19 21:00:00         False
96432  B09ZD4LFR3  486.9 2023-03-19 21:00:00         False
213.01999999999998
--------------------------------------------
------

             asin  price                time  buyBoxWinner
96682  B09ZHZGM8Q  60.01 2023-03-19 22:00:00         False
3.3299999999999983
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
96684  B09ZHZGM8Q  56.68 2023-03-19 23:00:00          True
             asin  price                time  buyBoxWinner
96685  B09ZHZGM8Q  60.01 2023-03-19 23:00:00         False
3.3299999999999983
--------------------------------------------
--------------------------------------------
             asin  price       time  buyBoxWinner
96687  B09ZHZGM8Q  56.68 2023-03-20          True
             asin  price       time  buyBoxWinner
96688  B09ZHZGM8Q  60.01 2023-03-20         False
3.3299999999999983
--------------------------------------------
--------------------------------------------
             asin   price                time  buyBoxWinner
96690  B09ZJBPQTZ  179.97 2023-03-19 13:00:00          True

             asin  price                time  buyBoxWinner
99432  B0BKQYYMLH  98.72 2023-03-19 23:00:00          True
99433  B0BKQYYMLH  98.72 2023-03-19 23:00:00         False
0.0
--------------------------------------------
--------------------------------------------
             asin  price       time  buyBoxWinner
99434  B0BKQYYMLH  98.72 2023-03-20          True
             asin  price       time  buyBoxWinner
99434  B0BKQYYMLH  98.72 2023-03-20          True
99435  B0BKQYYMLH  98.72 2023-03-20         False
0.0
--------------------------------------------
--------------------------------------------
             asin  price                time  buyBoxWinner
99436  B0BKXT1X16  178.0 2023-03-19 13:00:00          True
             asin  price                time  buyBoxWinner
99438  B0BKXT1X16  184.9 2023-03-19 13:00:00         False
6.900000000000006
--------------------------------------------
--------------------------------------------
             asin  price                t

In [114]:
# Print the results
print("Highest Difference:", highest_difference)
print("Highest Difference Row/Asin:", highest_difference_row)

Highest Difference: 484.0
Highest Difference Row/Asin: ('B08WPV9RM7', Timestamp('2023-03-19 17:00:00', freq='H'))


## Prozentualer Unterschied zwischen minimalen und maximalen Preis

In [115]:
# Convert the 'time' column to a DatetimeIndex
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Group the DataFrame by 'asin' and time slot (hour)
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the average percentage difference between the Price of the buyBoxWinning Row and the most expensive row
def avg_price_diff(group):
    # Get the row with the highest price
    highest_price_row = group.loc[group['price'] == group['price'].max()]
    highest_price = highest_price_row.iloc[0]['price']
    
    # Get the row with the buyBox winning offer
    buyBox_winner_row = group.loc[group['buyBoxWinner'] == True]
    
    # Check if there is a buyBox winner for the group
    if buyBox_winner_row.empty:
        return None
    
    # Get the price of the buyBox winning offer
    buyBox_winner_price = buyBox_winner_row.iloc[0]['price']
    
    # Calculate the percentage difference between the highest price and the buyBox winning price
    diff_percent = ((highest_price - buyBox_winner_price) / highest_price) * 100
    
    # Return the percentage difference
    return diff_percent

# Apply the custom function to each group
price_diffs = grouped_df.apply(avg_price_diff)

# Drop the groups where there is no buyBox winner
price_diffs = price_diffs.dropna()

# Calculate the overall average percentage difference
overall_avg_diff = price_diffs.mean()

# Print the overall average percentage difference
print(overall_avg_diff)


22.31552897919766


In [116]:
df.head()

asin                time       id  price currency  \
0  B00000JD6K 2023-03-19 13:00:00   1919.0   95.0        €   
1  B00000JD6K 2023-03-19 13:00:00   2375.0   86.9        €   
2  B00000JD6K 2023-03-19 14:00:00  11131.0   95.8        €   
3  B00000JD6K 2023-03-19 14:00:00  11585.0   86.9        €   
4  B00000JD6K 2023-03-19 15:00:00  20373.0   95.8        €   

                    crawlTime condition                 sellerName  \
0  2023-03-19 13:31:27.889305       Neu                      Kidia   
1  2023-03-19 13:31:28.080901       Neu  STILE IMMAGINE DIGITAL HD   
2  2023-03-19 14:36:46.595551       Neu                      Kidia   
3  2023-03-19 14:36:46.805501       Neu  STILE IMMAGINE DIGITAL HD   
4  2023-03-19 15:43:49.220017       Neu                      Kidia   

         sellerId  sellerbewertung  ...  lieferpreis  \
0  A2XUKJNGI8V9XU            46.56  ...          0.0   
1  A16E8RFMSALSSB            28.13  ...          9.9   
2  A2XUKJNGI8V9XU            46.56  ...          0.0   
3  A16E8RFMSALSSB            28.13  ...          9.9   
4  A2XUKJNGI8V9XU            46.56  ...          0.0   

             lieferung_durch  ranking buyBoxWinner  numberOfSellers  \
0                     Amazon      0.0         True              2.0   
1  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
2                     Amazon      0.0         True              2.0   
3  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
4                     Amazon      0.0         True              2.0   

   trigByReactive  time_gap  copyed_cause_missing  Fulfillment_type  date_diff  
0           False       0.0                 False               FBA        3.0  
1           False       0.0                 False               FBM        7.0  
2           False       0.0                 False               FBA        3.0  
3           False       0.0                 False               FBM       27.0  
4           False       0.0                 False               FBA        3.0  

[5 rows x 22 columns]

In [117]:
df.tail()

asin                time       id  price currency  \
109318  B0BNC8RXH1 2023-03-19 18:00:00  39396.0  44.95        €   
109319  B0BNC8RXH1 2023-03-19 18:00:00  39397.0  46.99        €   
109320  B0BNC8RXH1 2023-03-19 18:00:00  39398.0  43.36        €   
109321  B0BNC8RXH1 2023-03-19 18:00:00  39399.0  36.89        €   
109322  B0BNC8RXH1 2023-03-19 18:00:00  39400.0  42.99        €   

                         crawlTime condition  \
109318  2023-03-19 17:58:12.228703       New   
109319  2023-03-19 17:58:12.229013       New   
109320  2023-03-19 17:58:12.229350       New   
109321  2023-03-19 17:58:12.229680       New   
109322  2023-03-19 17:58:12.229983       New   

                               sellerName        sellerId  sellerbewertung  \
109318                      BERSERK MEDIA  A2I0YUYMTP72AW           460.75   
109319  Brickcomplete - Rasche Lieferung!  A161UJEV1LEUDQ           505.92   
109320                    Taschengelddieb  A2ABL365H1I2MT           284.16   
109321    Renax Toys - Schnelle Lieferung   AY2P88IIOMU8N           233.59   
109322                          ms-plueth  A377LN9JZ1QB15           304.78   

        ...  lieferpreis                    lieferung_durch  ranking  \
109318  ...         7.00                      BERSERK MEDIA      2.0   
109319  ...         6.36  Brickcomplete - Rasche Lieferung!      3.0   
109320  ...        12.99                    Taschengelddieb      4.0   
109321  ...        22.00    Renax Toys - Schnelle Lieferung      5.0   
109322  ...        17.95                          ms-plueth      6.0   

       buyBoxWinner  numberOfSellers  trigByReactive  time_gap  \
109318        False              6.0           False      -1.0   
109319        False              6.0           False      -1.0   
109320        False              6.0           False      -1.0   
109321        False              6.0           False      -1.0   
109322        False              6.0           False      -1.0   

        copyed_cause_missing  Fulfillment_type  date_diff  
109318                  True               FBM       32.0  
109319                  True               FBM        NaN  
109320                  True               FBM        NaN  
109321                  True               FBM        NaN  
109322                  True               FBM        NaN  

[5 rows x 22 columns]

In [118]:
df = pd.read_csv('cleaned_data.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109323 entries, 0 to 109322
Data columns (total 22 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   asin                  109323 non-null  object 
 1   time                  109323 non-null  object 
 2   id                    109323 non-null  float64
 3   price                 109323 non-null  float64
 4   currency              109323 non-null  object 
 5   crawlTime             109323 non-null  object 
 6   condition             109323 non-null  object 
 7   sellerName            109323 non-null  object 
 8   sellerId              109323 non-null  object 
 9   sellerbewertung       82422 non-null   float64
 10  seller_sterne         109323 non-null  float64
 11  lieferdatum           105495 non-null  object 
 12  lieferpreis           105495 non-null  float64
 13  lieferung_durch       109323 non-null  object 
 14  ranking               109323 non-null  float64
 15  

In [119]:
## Exclude all Rows where condition isnt New and which where a reactive Crawl
df = df[df['trigByReactive'] != True]
df = df[df['condition'].isin(['Neu', 'New'])]

In [120]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 88501 entries, 0 to 109322
Data columns (total 22 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   asin                  88501 non-null  object 
 1   time                  88501 non-null  object 
 2   id                    88501 non-null  float64
 3   price                 88501 non-null  float64
 4   currency              88501 non-null  object 
 5   crawlTime             88501 non-null  object 
 6   condition             88501 non-null  object 
 7   sellerName            88501 non-null  object 
 8   sellerId              88501 non-null  object 
 9   sellerbewertung       80095 non-null  float64
 10  seller_sterne         88501 non-null  float64
 11  lieferdatum           85019 non-null  object 
 12  lieferpreis           85019 non-null  float64
 13  lieferung_durch       88501 non-null  object 
 14  ranking               88501 non-null  float64
 15  buyBoxWinner      

## Wie lange hält ein Verkäufer die BuyBox im Schnitt

In [121]:
### Maybe i should filter out Asins where One Hour is Missing. Or i just make a copy of the Prices in the Hour before.

In [122]:
import pandas as pd

# Assuming you already have a dataframe called df

# Group the dataframe by 'asin' and sort the rows within each group by the 'time' column
df_grouped = df.groupby('asin', group_keys=False).apply(lambda x: x.sort_values('time'))

# If you want to reset the index of the resulting dataframe, you can use the reset_index method
df_grouped = df_grouped.reset_index(drop=True)

# Print the sorted dataframe
df_grouped.head()


asin                 time       id  price currency  \
0  B00000JD6K  2023-03-19 13:00:00   1919.0   95.0        €   
1  B00000JD6K  2023-03-19 13:00:00   2375.0   86.9        €   
2  B00000JD6K  2023-03-19 14:00:00  11131.0   95.8        €   
3  B00000JD6K  2023-03-19 14:00:00  11585.0   86.9        €   
4  B00000JD6K  2023-03-19 15:00:00  20373.0   95.8        €   

                    crawlTime condition                 sellerName  \
0  2023-03-19 13:31:27.889305       Neu                      Kidia   
1  2023-03-19 13:31:28.080901       Neu  STILE IMMAGINE DIGITAL HD   
2  2023-03-19 14:36:46.595551       Neu                      Kidia   
3  2023-03-19 14:36:46.805501       Neu  STILE IMMAGINE DIGITAL HD   
4  2023-03-19 15:43:49.220017       Neu                      Kidia   

         sellerId  sellerbewertung  ...  lieferpreis  \
0  A2XUKJNGI8V9XU            46.56  ...          0.0   
1  A16E8RFMSALSSB            28.13  ...          9.9   
2  A2XUKJNGI8V9XU            46.56  ...          0.0   
3  A16E8RFMSALSSB            28.13  ...          9.9   
4  A2XUKJNGI8V9XU            46.56  ...          0.0   

             lieferung_durch  ranking buyBoxWinner  numberOfSellers  \
0                     Amazon      0.0         True              2.0   
1  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
2                     Amazon      0.0         True              2.0   
3  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
4                     Amazon      0.0         True              2.0   

   trigByReactive  time_gap  copyed_cause_missing  Fulfillment_type  date_diff  
0           False       0.0                 False               FBA        3.0  
1           False       0.0                 False               FBM        7.0  
2           False       0.0                 False               FBA        3.0  
3           False       0.0                 False               FBM       27.0  
4           False       0.0                 False               FBA        3.0  

[5 rows x 22 columns]

In [123]:
df.head()

asin                 time       id  price currency  \
0  B00000JD6K  2023-03-19 13:00:00   1919.0   95.0        €   
1  B00000JD6K  2023-03-19 13:00:00   2375.0   86.9        €   
2  B00000JD6K  2023-03-19 14:00:00  11131.0   95.8        €   
3  B00000JD6K  2023-03-19 14:00:00  11585.0   86.9        €   
4  B00000JD6K  2023-03-19 15:00:00  20373.0   95.8        €   

                    crawlTime condition                 sellerName  \
0  2023-03-19 13:31:27.889305       Neu                      Kidia   
1  2023-03-19 13:31:28.080901       Neu  STILE IMMAGINE DIGITAL HD   
2  2023-03-19 14:36:46.595551       Neu                      Kidia   
3  2023-03-19 14:36:46.805501       Neu  STILE IMMAGINE DIGITAL HD   
4  2023-03-19 15:43:49.220017       Neu                      Kidia   

         sellerId  sellerbewertung  ...  lieferpreis  \
0  A2XUKJNGI8V9XU            46.56  ...          0.0   
1  A16E8RFMSALSSB            28.13  ...          9.9   
2  A2XUKJNGI8V9XU            46.56  ...          0.0   
3  A16E8RFMSALSSB            28.13  ...          9.9   
4  A2XUKJNGI8V9XU            46.56  ...          0.0   

             lieferung_durch  ranking buyBoxWinner  numberOfSellers  \
0                     Amazon      0.0         True              2.0   
1  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
2                     Amazon      0.0         True              2.0   
3  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
4                     Amazon      0.0         True              2.0   

   trigByReactive  time_gap  copyed_cause_missing  Fulfillment_type  date_diff  
0           False       0.0                 False               FBA        3.0  
1           False       0.0                 False               FBM        7.0  
2           False       0.0                 False               FBA        3.0  
3           False       0.0                 False               FBM       27.0  
4           False       0.0                 False               FBA        3.0  

[5 rows x 22 columns]

In [124]:
# Convert the 'time' column to datetime type
df["time"] = pd.to_datetime(df["time"], format="%Y-%m-%d %H:%M:%S")

In [125]:
import pandas as pd

# Assuming you already have a dataframe called df

# Convert the 'time' column to datetime type with the specified format
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Filter the rows where 'buyBoxWinner' is True
winning_rows = df[df['buyBoxWinner']]

# Sort the winning rows by 'asin' and 'time'
winning_rows = winning_rows.sort_values(['asin', 'time'])

# Calculate the time difference between consecutive winning rows for each ASIN
winning_rows['time_diff'] = winning_rows.groupby('asin')['time'].diff()

# Only include time differences greater than 0
winning_rows = winning_rows[winning_rows['time_diff'].dt.total_seconds() > 0]

# Aggregate the time differences by ASIN and by 'sellerName'
time_agg = winning_rows.groupby(['asin', 'sellerName'])['time_diff'].sum().reset_index()

# Calculate the average winning time across all sellers who win the BuyBox
average_winning_time = time_agg['time_diff'].mean()

# Calculate the minimum, and maximum winning time across all groups
min_winning_time = time_agg['time_diff'].min()
max_winning_time = time_agg['time_diff'].max()

# Find the seller with the longest BuyBox holding time
longest_buybox_holder = time_agg.loc[time_agg['time_diff'].idxmax(), 'sellerName']

print("Average winning time:", average_winning_time)
print("Minimum winning time:", min_winning_time)
print("Maximum winning time:", max_winning_time)
print("Seller holding the BuyBox the longest:", longest_buybox_holder)


Average winning time: 0 days 08:48:58.432835820
Minimum winning time: 0 days 01:00:00
Maximum winning time: 0 days 11:00:00
Seller holding the BuyBox the longest: Kidia


In [126]:
import pandas as pd

# Assuming you already have a dataframe called df

# Convert the 'time' column to datetime type with the specified format
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Filter the rows where 'buyBoxWinner' is True
winning_rows = df[df['buyBoxWinner']]

# Sort the winning rows by 'asin' and 'time'
winning_rows = winning_rows.sort_values(['asin', 'time'])

# Calculate the time difference between consecutive winning rows for each ASIN
winning_rows['time_diff'] = winning_rows.groupby('asin')['time'].diff()

# Only include time differences greater than 0
winning_rows = winning_rows[winning_rows['time_diff'].dt.total_seconds() > 0]

# Aggregate the time differences by ASIN and by 'sellerName'
time_agg = winning_rows.groupby(['asin', 'sellerName'])['time_diff'].sum().reset_index()

# Calculate the average winning time across all sellers who win the BuyBox
average_winning_time = time_agg['time_diff'].mean()

# Calculate the minimum, and maximum winning time across all groups
min_winning_time = time_agg['time_diff'].min()
max_winning_time = time_agg['time_diff'].max()

# Find the seller with the longest BuyBox holding time
longest_buybox_holder = time_agg.loc[time_agg['time_diff'].idxmax(), 'sellerName']

# Filter sellers with winning time longer than 9 hours
sellers_longer_than_9_hours = time_agg[time_agg['time_diff'] > pd.Timedelta(hours=4)]

print("Average winning time:", average_winning_time)
print("Minimum winning time:", min_winning_time)
print("Maximum winning time:", max_winning_time)
print("Seller holding the BuyBox the longest:", longest_buybox_holder)
print("\nSellers with winning time longer than 9 hours:")

for index, row in sellers_longer_than_9_hours.iterrows():
    print(f"ASIN: {row['asin']}, Seller: {row['sellerName']}, Winning Time: {row['time_diff']}")


Average winning time: 0 days 08:48:58.432835820
Minimum winning time: 0 days 01:00:00
Maximum winning time: 0 days 11:00:00
Seller holding the BuyBox the longest: Kidia

Sellers with winning time longer than 9 hours:
ASIN: B00000JD6K, Seller: Kidia, Winning Time: 0 days 11:00:00
ASIN: B00005KIRS, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B00008K61M, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B00008K61N, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B0000C72GD, Seller: STILE IMMAGINE DIGITAL HD, Winning Time: 0 days 11:00:00
ASIN: B0000D85OD, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B0000WOK04, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B0001GRVJQ, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B00022749Q, Seller: amazon, Winning Time: 0 days 11:00:00
ASIN: B0002CZU1U, Seller: Musikhaus Kirstein GmbH, Winning Time: 0 days 11:00:00
ASIN: B0002CZYW0, Seller: HeBa - Sound & Music, Winning Time: 0 days 07:00:00
ASIN: B0002E1O68, Seller: amaz

In [127]:
#Always Test your Results
# boolean indexing to filter rows
result_df = df[(df['asin'] == 'B09R1WSCP2') & (df['buyBoxWinner'] == True)]

# print the filtered dataframe
result_df

asin                time       id  price currency  \
90594   B09R1WSCP2 2023-03-19 13:00:00     47.0  29.94        €   
90600   B09R1WSCP2 2023-03-19 14:00:00   9300.0  29.94        €   
90606   B09R1WSCP2 2023-03-19 15:00:00  18461.0  29.94        €   
90612   B09R1WSCP2 2023-03-19 16:00:00  27756.0  29.69        €   
90615   B09R1WSCP2 2023-03-19 17:00:00  36973.0  29.94        €   
90621   B09R1WSCP2 2023-03-19 19:00:00  46163.0  29.69        €   
90628   B09R1WSCP2 2023-03-19 20:00:00  55334.0  29.94        €   
90634   B09R1WSCP2 2023-03-19 21:00:00  64679.0  29.94        €   
90640   B09R1WSCP2 2023-03-19 22:00:00  73889.0  29.94        €   
90646   B09R1WSCP2 2023-03-19 23:00:00  83068.0  29.94        €   
90652   B09R1WSCP2 2023-03-20 00:00:00  92270.0  29.94        €   
108445  B09R1WSCP2 2023-03-19 18:00:00  36973.0  29.94        €   

                         crawlTime condition sellerName        sellerId  \
90594   2023-03-19 13:30:27.056754       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90600   2023-03-19 14:35:42.440560       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90606   2023-03-19 15:41:51.969087       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90612   2023-03-19 16:51:46.424649       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90615   2023-03-19 17:57:11.765450       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90621   2023-03-19 19:02:33.709976       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90628   2023-03-19 20:07:54.582202       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90634   2023-03-19 21:35:49.198177       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90640   2023-03-19 22:41:24.270829       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90646   2023-03-19 23:46:38.462121       Neu  bzoptical  A2CBTQ0B1XJ6AL   
90652   2023-03-20 00:52:13.018262       Neu  bzoptical  A2CBTQ0B1XJ6AL   
108445  2023-03-19 17:57:11.765450       Neu  bzoptical  A2CBTQ0B1XJ6AL   

        sellerbewertung  ...  lieferpreis lieferung_durch  ranking  \
90594            458.35  ...          0.0          Amazon      0.0   
90600            458.35  ...          0.0          Amazon      0.0   
90606            458.35  ...          0.0          Amazon      0.0   
90612            458.35  ...          0.0          Amazon      0.0   
90615            458.35  ...          0.0          Amazon      0.0   
90621            458.35  ...          0.0          Amazon      0.0   
90628            458.35  ...          0.0          Amazon      0.0   
90634            458.35  ...          0.0          Amazon      0.0   
90640            458.35  ...          0.0          Amazon      0.0   
90646            458.35  ...          0.0          Amazon      0.0   
90652            458.35  ...          0.0          Amazon      0.0   
108445           458.35  ...          0.0          Amazon      0.0   

       buyBoxWinner  numberOfSellers  trigByReactive  time_gap  \
90594          True              6.0           False       0.0   
90600          True              6.0           False       0.0   
90606          True              6.0           False       0.0   
90612          True              3.0           False       0.0   
90615          True              6.0           False       0.0   
90621          True              7.0           False       0.0   
90628          True              6.0           False       0.0   
90634          True              6.0           False       0.0   
90640          True              6.0           False       0.0   
90646          True              6.0           False       0.0   
90652          True              6.0           False       0.0   
108445         True              6.0           False      -1.0   

        copyed_cause_missing  Fulfillment_type  date_diff  
90594                  False               FBA        3.0  
90600                  False               FBA        3.0  
90606                  False               FBA        3.0  
90612                  False               FBA        3.0  
90615                  False               FBA        3.0  
90621                  False        

## Price changes while winning the BuyBox?

In [128]:
import pandas as pd

# Assuming your DataFrame is named df

# 1. Filter out the rows where buyBoxWinner is True
winning_rows = df[df['buyBoxWinner']]

# 2. Group the data by asin and sellerName
grouped = winning_rows.groupby(['asin', 'sellerName'])

# 3. Calculate the number of price changes for each group
price_changes = grouped['price'].apply(lambda x: x.ne(x.shift()).sum()).reset_index(name='price_change_count')

# Merge price_changes back to the winning_rows dataframe
winning_rows = winning_rows.merge(price_changes, on=['asin', 'sellerName'])

# 4. Calculate the average and maximum number of price changes
avg_price_changes = winning_rows['price_change_count'].mean()
max_price_changes = winning_rows['price_change_count'].max()

print(f"Average price changes: {avg_price_changes}")
print(f"Maximum price changes: {max_price_changes}")

# 5. Calculate the average percent difference in price changes
winning_rows['price_pct_change'] = winning_rows.groupby(['asin', 'sellerName'])['price'].pct_change()
avg_pct_diff = winning_rows['price_pct_change'].mean() * 100

print(f"Average percent difference in price changes: {avg_pct_diff}%")

# 6. Find the seller with the most price changes and print their rows
max_changes_seller = winning_rows.loc[winning_rows['price_change_count'] == max_price_changes]
max_seller_name = max_changes_seller['sellerName'].iloc[0]
max_seller_asin = max_changes_seller['asin'].iloc[0]

print(f"Seller with most price changes: {max_seller_name}, ASIN: {max_seller_asin}")

max_seller_rows = winning_rows[(winning_rows['sellerName'] == max_seller_name) & (winning_rows['asin'] == max_seller_asin)]
print("Rows where the seller with the most price changes updates their price:")
max_seller_rows




Average price changes: 3.432512025130068
Maximum price changes: 12
Average percent difference in price changes: 0.006259054156726982%
Seller with most price changes: Bambelaa!, ASIN: B08DJ91P4Q
Rows where the seller with the most price changes updates their price:


asin                time       id  price currency  \
7009  B08DJ91P4Q 2023-03-19 13:00:00   3923.0  58.42        €   
7010  B08DJ91P4Q 2023-03-19 14:00:00  13107.0  58.40        €   
7011  B08DJ91P4Q 2023-03-19 15:00:00  22358.0  58.51        €   
7012  B08DJ91P4Q 2023-03-19 16:00:00  31560.0  58.38        €   
7013  B08DJ91P4Q 2023-03-19 17:00:00  40795.0  58.37        €   
7014  B08DJ91P4Q 2023-03-19 19:00:00  49980.0  58.49        €   
7015  B08DJ91P4Q 2023-03-19 20:00:00  57266.0  58.48        €   
7016  B08DJ91P4Q 2023-03-19 21:00:00  68487.0  58.35        €   
7017  B08DJ91P4Q 2023-03-19 22:00:00  77685.0  58.33        €   
7018  B08DJ91P4Q 2023-03-19 23:00:00  86906.0  58.57        €   
7019  B08DJ91P4Q 2023-03-20 00:00:00  96086.0  58.54        €   
7020  B08DJ91P4Q 2023-03-19 18:00:00  40795.0  58.37        €   

                       crawlTime condition sellerName        sellerId  \
7009  2023-03-19 13:32:28.725512       Neu  Bambelaa!  A1LCL7QG85GMWX   
7010  2023-03-19 14:37:48.901080       Neu  Bambelaa!  A1LCL7QG85GMWX   
7011  2023-03-19 15:46:15.126748       Neu  Bambelaa!  A1LCL7QG85GMWX   
7012  2023-03-19 16:53:54.927305       Neu  Bambelaa!  A1LCL7QG85GMWX   
7013  2023-03-19 17:59:12.267197       Neu  Bambelaa!  A1LCL7QG85GMWX   
7014  2023-03-19 19:04:36.692634       New  Bambelaa!  A1LCL7QG85GMWX   
7015  2023-03-19 20:32:15.424537       Neu  Bambelaa!  A1LCL7QG85GMWX   
7016  2023-03-19 21:38:02.732700       Neu  Bambelaa!  A1LCL7QG85GMWX   
7017  2023-03-19 22:43:29.326512       Neu  Bambelaa!  A1LCL7QG85GMWX   
7018  2023-03-19 23:48:40.782332       Neu  Bambelaa!  A1LCL7QG85GMWX   
7019  2023-03-20 00:54:13.681177       Neu  Bambelaa!  A1LCL7QG85GMWX   
7020  2023-03-19 17:59:12.267197       Neu  Bambelaa!  A1LCL7QG85GMWX   

      sellerbewertung  ...  ranking buyBoxWinner  numberOfSellers  \
7009          6049.54  ...      0.0         True              2.0   
7010          6049.54  ...      0.0         True              2.0   
7011          6049.54  ...      0.0         True              5.0   
7012          6049.54  ...      0.0         True              2.0   
7013          6049.54  ...      0.0         True              2.0   
7014          6049.54  ...      0.0         True              2.0   
7015          6049.54  ...      0.0         True              2.0   
7016          6049.54  ...      0.0         True              2.0   
7017          6049.54  ...      0.0         True              2.0   
7018          6049.54  ...      0.0         True              2.0   
7019          6049.54  ...      0.0         True              2.0   
7020          6049.54  ...      0.0         True              2.0   

     trigByReactive  time_gap  copyed_cause_missing  Fulfillment_type  \
7009          False       0.0                 False               FBA   
7010          False       0.0                 False               FBA   
7011          False       0.0                 False               FBA   
7012          False       0.0                 False               FBA   
7013          False       0.0                 False               FBA   
7014          False       0.0                 False               FBA   
7015          False       0.0                 False               FBA   
7016          False       0.0                 False               FBA   
7017          False       0.0                 False               FBA   
7018          False       0.0                 False               FBA   
7019          False       0.0                 False               FBA   
7020          False      -1.0                  True               FBA   

      date_diff  price_change_count  price_pct_change  
7009        3.0                  12               NaN  
7010        3.0                  12         -0.000342  
7011        3.0                  12          0.001884  
7012        3.0                  12         -0.002222  
7013        3.0                  12         -0.000171  
7014        NaN                 

In [129]:
max_seller_rows.to_csv('Seller_changing_price_often.csv', index=False)